In [68]:
import os
import numpy as np
import pandas as pd
import pickle
import quandl
from datetime import datetime as dt

import plotly.offline as plo
import plotly.graph_objs as pgo
import plotly.figure_factory as pff
plo.init_notebook_mode(connected=True)

In [5]:
#API key for Quandl
quandl.ApiConfig.api_key = "aoysDcHfVqeAg9efRtsC"
#Pull data as series from Quandl API and cache it with pickle.
def pull_quandl_data(quandl_id):
    cache_path = '{}.pk1'.format(quandl_id).replace('/','-')
    try: #Will run successfully if pk file has already been created.
        f = open(cache_path, 'rb')
        df = pickle.load(f)  
        print('Loaded from cache' .format(quandl_id))
    except(OSError, IOError) as error: #will run when Pk file does not exist, and download then create new pk file from df
        print('Downloading {} from Quandl' .format(quandl_id))
        df=quandl.get(quandl_id, returns="pandas")
        df.to_pickle(cache_path)
        print('Cached {} at {}' .format(quandl_id, cache_path))
    return df 

In [6]:
#Pulling exchange data 
kraken_btc_price_usd = pull_quandl_data('BCHARTS/KRAKENUSD')

Cached BCHARTS/KRAKENUSD at BCHARTS-KRAKENUSD.pk1


In [7]:
#Check head
kraken_btc_price_usd.head()

Open       High        Low      Close  Volume (BTC)  \
Date                                                                   
2014-01-07  874.67040  892.06753  810.00000  810.00000     15.622378   
2014-01-08  810.00000  899.84281  788.00000  824.98287     19.182756   
2014-01-09  825.56345  870.00000  807.42084  841.86934      8.158335   
2014-01-10  839.99000  857.34056  817.00000  857.33056      8.024510   
2014-01-11  858.20000  918.05471  857.16554  899.84105     18.748285   

            Volume (Currency)  Weighted Price  
Date                                           
2014-01-07       13151.472844      841.835522  
2014-01-08       16097.329584      839.156269  
2014-01-09        6784.249982      831.572913  
2014-01-10        6780.220188      844.938794  
2014-01-11       16698.566929      890.671709

In [9]:
#Create simple chart
btc_chart = pgo.Scatter(x=kraken_btc_price_usd.index, y=kraken_btc_price_usd['Weighted Price'])
plo.iplot([btc_chart])

In [11]:
#Add price data from more BTC exchanges into dict of dataframes.
exchanges = ['Coinbase', 'Bitstamp', 'Cbx', 'ITBIT'] # see https://blog.quandl.com/api-for-bitcoin-data for a full list.
exchange_data = {}
exchange_data['KRAKEN'] = kraken_btc_price_usd

for e in exchanges:
    exchange_code = 'BCHARTS/{}USD'.format(e)
    btc_exchange_df = pull_quandl_data(exchange_code)
    exchange_data[e] = btc_exchange_df

Cached BCHARTS/CoinbaseUSD at BCHARTS-CoinbaseUSD.pk1
Cached BCHARTS/BitstampUSD at BCHARTS-BitstampUSD.pk1
Cached BCHARTS/CbxUSD at BCHARTS-CbxUSD.pk1
Cached BCHARTS/ITBITUSD at BCHARTS-ITBITUSD.pk1


In [14]:
#Merging of dataframes into one combined DF. Merges single column of each DF into a new combined DF
def merge_dfs_at_column(dataframes, labels, col):
    series_merged = {}
    for i in range(len(dataframes)):
        series_merged[labels[i]] = dataframes[i][col]
    return pd.DataFrame(series_merged)

In [31]:
#Merge BTC dataseires into single DF on "Weighted Price" col
btc_usd_datasets = merge_dfs_at_column(list(exchange_data.values()), list(exchange_data.keys()), 'Weighted Price')

In [32]:
btc_usd_datasets.tail()


KRAKEN  Coinbase     Bitstamp  Cbx  ITBIT
Date                                                      
2020-03-02  8782.699022       NaN  8785.287904  NaN    NaN
2020-03-03  8774.187278       NaN  8782.757838  NaN    NaN
2020-03-04  8754.966621       NaN  8750.230527  NaN    NaN
2020-03-05  9022.404690       NaN  9035.268235  NaN    NaN
2020-03-06  9062.607186       NaN  9057.901465  NaN    NaN

In [58]:
#Function to generate price comparison chart from dataframe.
def df_scatterplot(df, title, seperate_y_axis=False, y_axis_label='', scale='linear', inital_hide=False):
    ar_label = list(df)
    ar_series = list(map(lambda col: df[col], ar_label))
    
    layout = pgo.Layout(
        title = title,
        legend = dict(orientation="h"),
        xaxis = dict(type='date'),
        yaxis =dict(
            title = y_axis_label,
            showticklabels = not seperate_y_axis,
            type = scale
        )
    )
    
    config_y_axis = dict(
        overlaying ='y',
        showticklabels = False,
        type = scale
    )
    
    visibility = True
    if inital_hide:
        visibility = 'legendonly'
    
    #Trace for each series form
    ar_trace = []
    for i, series in enumerate(ar_series):
        trace = pgo.Scatter(
            x = series.index,
            y = series,
            name = ar_label[i],
            visible = visibility
        )
        
        #axis for series if seperate
        if seperate_y_axis:
            trace['yaxis'] = 'y{}'.format(i+1)
            layout['yaxis{}'.format(i+1)] = y_axis_config
        ar_trace.append(trace)
        
    figure = pgo.Figure(data=ar_trace, layout=layout)
    plo.iplot(figure)
    

In [55]:
#test above function to plot all btc price data.
df_scatterplot(btc_usd_datasets, 'BTC USD Price by Exchange')

In [56]:
#Cleaning up the data, removing 0 values
btc_usd_datasets.replace(0, np.nan, inplace=True)

In [60]:
#Chart again to see if changes made correctly
df_scatterplot(btc_usd_datasets, 'BTC USD Price by Exchange')

In [62]:
#Create new column for avg BTC price
btc_usd_datasets['avg_price_usd'] = btc_usd_datasets.mean(axis=1)

In [63]:
#Chart only the avg price
btc_trace = pgo.Scatter(x=btc_usd_datasets.index, y=btc_usd_datasets['avg_price_usd'])
plo.iplot([btc_trace])

In [ ]:
#BTC price series finished, now to do altcoins using Poloniex API.

In [66]:
#Download then cache JSON data, then return as DF
def json_data(json_url, cache_path):
        try:
            f = open(cache_path, 'rb')
            df = pickle.load(f)
            print('Loaded {} from cache'.format(json_url))
        except (OSError, IOError) as e:
            print('Downloading {}'.format(json_url))
            df = pd.read_json(json_url)
            df.to_pickle(cache_path)
            print('Cached response at {}'.format(json_url, cache_path))
        return df
            
    

In [70]:
#Get Poloniex API HTTO requests, save data using json_data()

url = 'https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}'
start_date = dt.strptime('2015-01-01', '%Y-%m-%d') #From beginning of 2015
end_date = dt.now() 
period = 86400 #daily data, as 86400 seconds/day

def pull_crypto_data(poloniex_pair):
    json_url = url.format(poloniex_pair, start_date.timestamp(), end_date.timestamp(), period)
    alt_df = json_data(json_url, poloniex_pair)
    alt_df = alt_df.set_index('date')
    return alt_df

In [85]:
#Download Data from Poloniex
#To find price of each coin, compare value to BTC data and convert accordingly

coins = ['ETH','XRP', 'LTC', 'BAT', 'XMR', 'EOS', 'TRX']

crypto_data = {}
for coin in coins:
    pair = 'BTC_{}'.format(coin)
    crypto_price_df = pull_crypto_data(pair)
    crypto_data[coin] = crypto_price_df

Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETH&start=1420088400.0&end=1583521485.782743&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_XRP&start=1420088400.0&end=1583521485.782743&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_LTC&start=1420088400.0&end=1583521485.782743&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_BAT&start=1420088400.0&end=1583521485.782743&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_XMR&start=1420088400.0&end=1583521485.782743&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_EOS&start=1420088400.0&end=1583521485.782743&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_TRX&start=1420088400.0&end=1583521485.782743&period=86

In [86]:
crypto_data['ETH'].tail()


high       low      open     close      volume   quoteVolume  \
date                                                                           
2020-03-02  0.026295  0.025411  0.025542  0.026020  398.936126  15420.558193   
2020-03-03  0.026134  0.025418  0.026020  0.025558  588.675704  22844.887647   
2020-03-04  0.025951  0.025389  0.025554  0.025629  675.564541  26352.608873   
2020-03-05  0.025749  0.025033  0.025629  0.025208  348.650046  13671.415952   
2020-03-06  0.026324  0.025193  0.025208  0.026212  436.032982  16814.364674   

            weightedAverage  
date                         
2020-03-02         0.025870  
2020-03-03         0.025768  
2020-03-04         0.025636  
2020-03-05         0.025502  
2020-03-06         0.025932

In [89]:
#Add new columns with USD price for each altcoin
for coin in crypto_data.keys():
    crypto_data[coin]['usd_price'] = crypto_data[coin]['weightedAverage'] * btc_usd_datasets['avg_price_usd']

In [92]:
#Create df of USD prices for each altcoin
merged_alts_df = merge_dfs_at_column(list(crypto_data.values()), list(crypto_data.keys()), 'usd_price' )

#Add BTC Price to the above df
merged_alts_df['BTC'] = btc_usd_datasets['avg_price_usd']



In [96]:
#Chart new DF using previous scatter function
df_scatterplot(merged_alts_df, "Crypto Prices (USD)", seperate_y_axis = False, y_axis_label='Coin Price (USD)', scale = 'log')

In [106]:
#Correlations by years
merged_alts_df_2016 = merged_alts_df[merged_alts_df.index.year == 2016]
merged_alts_df_2016.pct_change().corr(method='pearson')

#Correlations by year - 2017
merged_alts_df_2017 = merged_alts_df[merged_alts_df.index.year == 2017]
merged_alts_df_2017.pct_change().corr(method='pearson')

#Correlations by year - 2018
merged_alts_df_2018 = merged_alts_df[merged_alts_df.index.year == 2018]
merged_alts_df_2018.pct_change().corr(method='pearson')

#Correlations by year - 2019
merged_alts_df_2019 = merged_alts_df[merged_alts_df.index.year == 2019]
merged_alts_df_2019.pct_change().corr(method='pearson')

#Correlations by year - 2020
merged_alts_df_2020 = merged_alts_df[merged_alts_df.index.year == 2020]
merged_alts_df_2020.pct_change().corr(method='pearson')


ETH       XRP       LTC       BAT       XMR       EOS       TRX  \
ETH  1.000000  0.877912  0.837585  0.778533  0.795323  0.768006  0.880291   
XRP  0.877912  1.000000  0.774951  0.706564  0.753679  0.705663  0.848426   
LTC  0.837585  0.774951  1.000000  0.718521  0.784827  0.835387  0.809223   
BAT  0.778533  0.706564  0.718521  1.000000  0.692562  0.720076  0.821538   
XMR  0.795323  0.753679  0.784827  0.692562  1.000000  0.688520  0.792608   
EOS  0.768006  0.705663  0.835387  0.720076  0.688520  1.000000  0.746489   
TRX  0.880291  0.848426  0.809223  0.821538  0.792608  0.746489  1.000000   
BTC  0.790800  0.717536  0.843967  0.660254  0.786527  0.781710  0.782294   

          BTC  
ETH  0.790800  
XRP  0.717536  
LTC  0.843967  
BAT  0.660254  
XMR  0.786527  
EOS  0.781710  
TRX  0.782294  
BTC  1.000000

In [107]:
#Heatmap Function for correlations
def corr_heatmap(df, title, absolute_bounds = True):
    heatmap = pgo.Heatmap(
        z = df.corr(method='pearson'),
        x = df.columns,
        y = df.columns,
        colorbar = dict(title='Pearson Coeffecient')
    )
    
    layout = pgo.Layout(title=title)
    if absolute_bounds:
        heatmap['zmax'] = 1.0
        heatmap['zmin'] = -1.0
    
    figure = pgo.Figure(data=[heatmap], layout=layout)
    plo.iplot(figure)


In [108]:
#Heatmaps for yers 2016-2020
corr_heatmap(merged_alts_df_2016.pct_change(), "Crypto Correlations - 2016")
corr_heatmap(merged_alts_df_2017.pct_change(), "Crypto Correlations - 2017")
corr_heatmap(merged_alts_df_2018.pct_change(), "Crypto Correlations - 2018")
corr_heatmap(merged_alts_df_2019.pct_change(), "Crypto Correlations - 2019")
corr_heatmap(merged_alts_df_2020.pct_change(), "Crypto Correlations - 2020")